In [10]:
import pandas as pd
import numpy as np
import os

from datetime import datetime

import yfinance as yf
import plotly.graph_objects as go

In [11]:
## Fetch Data
ticker_data = yf.download("EURUSD=X", period="60d", interval="5m")

ticker_data = ticker_data[["Open", "Close", "Low", "High"]]

[*********************100%***********************]  1 of 1 completed


In [12]:
# file = "audcad-1d"

# col_names = ['Date', 'Time', 'Open', 'High', 'Low', 'Close', 'Volume']

# raw_path = os.path.join(os.getcwd(), "d2", f'{file}.csv')
# updated_file_path = os.path.join(os.getcwd(), "d2/converted", f'{file}-updated.csv')

# exists = os.path.isfile(updated_file_path)

# args = {}

# if exists: 
#     args['parse_dates'] = True
#     args['index_col'] = 'Datetime'
    
# else:
#     args['sep'] = ';'
#     args['names'] = col_names
#     header=None

# print(exists, raw_path, updated_file_path)

# ticker_data = pd.read_csv(
#     updated_file_path if exists else raw_path , **args)


# def convert_date(row):
#     # print(row['Date']+' '+row['Time'])

#     row["Datetime"] = datetime.strptime(
#         row["Date"] + " " + row["Time"], "%d/%m/%Y %H:%M:%S"
#     )

#     return row

# if not exists: 
#     ticker_data = ticker_data.apply(convert_date, axis=1)
#     ticker_data.to_csv(updated_file_path)

# ticker_data

In [13]:
class Backtest:
    balance = 0
    start_balance = 0

    stoploss = 0
    target = 0

    position = {
        "entry_date": None,
        "entry_price": None,
        "exit_price": None,
        "exit_date": None,
        "target": None,
        "stoploss": None,
        "PnL": None,
        "crossover_type": None,
        "active": False,
        "size": None,
        "cost": None,
        "balance": None,
    }

    trade_book = pd.DataFrame(
        columns=[
            "entry_date",
            "entry_price",
            "exit_price",
            "exit_date",
            "target",
            "stoploss",
            "PnL",
            "crossover_type",
            "active",
            "size",
            "margin_used",
            "balance",
            "balance_on_open",
        ]
    )

    order_book = pd.DataFrame(
        columns=[
            "datetime",
            "entry_price",
            "price",
            "type",
            "stoploss",
            "target",
        ]
    )

    def __init__(self, balance, stoploss, reward_ratio):
        self.start_balance = balance
        self.balance = balance
        self.stoploss = stoploss
        self.target = stoploss * reward_ratio

        self.clear_position()
        self.reset_tradebook()

    def clear_position(self):
        self.position["entry_date"] = None
        self.position["entry_price"] = None
        self.position["exit_price"] = None
        self.position["exit_date"] = None

        self.position["target"] = None
        self.position["stoploss"] = None

        self.position["PnL"] = None
        self.position["crossover_type"] = None

        self.position["active"] = False
        self.position["size"] = 0
        self.position["balance"] = None

        self.position["status"] = None

    def reset_tradebook(self):
        self.trade_book = pd.DataFrame(
            columns=[
                "entry_date",
                "entry_price",
                "exit_price",
                "exit_date",
                "target",
                "stoploss",
                "PnL",
                "crossover_type",
                "active",
                "size",
                "margin_used",
                "balance",
                "opening_balance",
            ]
        )

    def open(self, entry_date, entry_price, stoploss, target, size, order_type):
        if self.balance is None or self.balance == 0:
            raise Exception("Oops, you ran out of bucks.")

        if self.balance < entry_price * size:
            print("Balance: ", self.balance)
            print("Lot Size: ", size)
            print("Ticket Price: ", entry_price * size)
            raise Exception("Oops, you are low on bucks.")
        
        # Place Order into the order book
        self.order_book.loc[len(self.order_book)] = {
            "datetime": entry_date,
            "price": entry_price,
            "type": order_type,
            "stoploss": stoploss,
            "target": target,
        }
        
        # Build a trade position
        position = {
            'active': True,
            'entry_date': entry_date,
            'entry_price': entry_price,
            'stoploss': stoploss,
            'target': target,
            'size': size,
            'margin_used': entry_price * size,
            'opening_balance': self.balance,
            'balance': self.balance - entry_price * size,
        }
        
        # Place the trade into the trade book, and update the balance
        self.trade_book.loc[len(self.trade_book)] = position
        self.balance = self.balance - entry_price * size
        

    def close(self, candle, exit_price, exit_date):
        # Closes the trade / position
        self.position["active"] = False
        self.position["exit_date"] = candle.name
        self.position["exit_price"] = exit_price
        self.position["PnL"] = (
            exit_price - self.position["entry_price"]
        ) * self.position["size"]

        if self.position["crossover_type"] == "short":
            self.position["PnL"] = -1 * self.position["PnL"]

        balance = (
            self.position["balance_on_open"]
            + self.position["margin_used"]
            + self.position["PnL"]
        )
        self.position["balance"] = balance
        self.balance = balance

        row = pd.Series(self.position)
        self.trade_book.loc[len(self.trade_book)] = row

        self.clear_position()

    def strategy():
        ## to be implemented in subclass
        pass

    def print(self):
        print(self.balance, self.stoploss, self.target)

In [14]:
class Tester(Backtest):
    ticker_data = None
    size = 10
    
    candles_count = 3
    sl_tracker = {
        'current_track': None
    }

    def __init__(self, balance, stoploss, reward_ratio):
        super().__init__(balance, stoploss, reward_ratio)
        self.ticker_data = None
        self.reset_tradebook()
        
        self.profitable_trades = None
        self.losing_trades = None

    def init(self, ticker_data, size, small_ema, large_ema):
        ticker_data["small_ema"] = (
            ticker_data["Close"].ewm(span=small_ema, adjust=False).mean()
        )

        ticker_data["large_ema"] = (
            ticker_data["Close"].ewm(span=large_ema, adjust=False).mean()
        )

        ticker_data["crossover_pos"] = np.where(
            ticker_data["small_ema"] > ticker_data["large_ema"], 1, 0
        )

        ticker_data["crosspoint"] = np.where(
            ticker_data["crossover_pos"] != ticker_data["crossover_pos"].shift(1),
            True,
            False,
        )
        
        self.small_ema = small_ema
        self.large_ema = large_ema
        self.ticker_data = None
        self.ticker_data = ticker_data
        self.size = size

    def chart(self, small_ema, large_ema):
        fig = go.Figure(
            data=[
                go.Candlestick(
                    x=ticker_data.index,
                    open=ticker_data["Open"],
                    high=ticker_data["High"],
                    low=ticker_data["Low"],
                    close=ticker_data["Close"],
                ),
                go.Scatter(
                    x=ticker_data.index,
                    y=ticker_data["small_ema"],
                    name=f"small_ema_{small_ema}",
                ),
                go.Scatter(
                    x=ticker_data.index,
                    y=ticker_data["large_ema"],
                    name=f"large_ema_{large_ema}",
                ),
            ]
        )

        fig.update_layout(xaxis_rangeslider_visible=False)
        fig.show()

    def print(self):
        print(self.position)

    def run(self):
        if self.ticker_data is None:
            raise Exception("No ticker data to run backtest on")
        
        # Skip first 200 candles
        start_index = self.large_ema

        while start_index < len(self.ticker_data):
            self.strategy(self.ticker_data.iloc[start_index])
            start_index += 1

    def stats(self):
        print("Data: ", file,"\n")
        print("Small EMA: ", self.small_ema,"\n")
        print("Large EMA: ", self.large_ema,"\n")
        print("Total Trades: ", len(self.trade_book),"\n")
        print("PnL: ", self.trade_book["PnL"].sum(),"\n")
        print("Initial Balance: ", self.start_balance,"\n")
        print("Trade Size: ", self.size,"\n")
        print("Stoploss: ", self.stoploss,"\n")
        print("Target: ", self.target,"\n")
        # print("Acc. Profit: ", self.trade_book["PnL"].sum() - self.start_balance)
        

        total_trades = len(self.trade_book)
        profitable_trades = self.trade_book[self.trade_book["PnL"] > 0]
        losing_trades = self.trade_book[self.trade_book["PnL"] < 0]
        win_percentage = len(profitable_trades) / total_trades * 100
        lose_percentage = len(losing_trades) / total_trades * 100
        
        
        print("Profitable Trades: ", len(profitable_trades),"\n")
        print("Losing Trades: ", len(losing_trades),"\n")
        print("Win Percentage: ", win_percentage,"\n")
        print("Lose Percentage: ", lose_percentage,"\n")
        print("Date Range: ", self.trade_book["entry_date"].iloc[0], " - ", self.trade_book["exit_date"].iloc[-1],"\n")

        self.profitable_trades = profitable_trades
        self.losing_trades = losing_trades

    def strategy(self, candle):
        if self.position["active"] == True:
            # check if target met or stoploss hit
            # calculate trade results, PnL
            # close position

            if self.position["crossover_type"] == "long":
                if candle["Low"] < self.position["stoploss"] and self.position["stoploss"] > self.position["Close"]:
                    self.close(candle, self.position["Close"], candle.name)
                    return

                if candle["High"] > self.position["target"]:
                    self.close(candle, self.position["target"], candle.name)
                    return

            if self.position["crossover_type"] == "short":
                if candle["High"] > self.position["stoploss"] and self.position["stoploss"] < self.position["Close"]:
                    self.close(candle, self.position["Close"], candle.name)
                    return

                if candle["Low"] < self.position["target"]:
                    self.close(candle, self.position["target"], candle.name)
                    return

            return

        if candle["crosspoint"] == True:
            entry_price = candle["Close"]
            crossover_type = "long" if candle["crossover_pos"] == 1 else "short"
            stoploss = None
            target = None
            
            if crossover_type == "short":
                stoploss = entry_price + self.stoploss
                target = entry_price - self.target
                
            if crossover_type == "long":
                stoploss = entry_price - self.stoploss
                target = entry_price + self.target

            self.open(
                entry_date=candle.name,
                entry_price=entry_price,
                stoploss=stoploss,
                target=target,
                size=self.size,
                crossover_type=crossover_type,
            )

In [15]:
small_ema =7
large_ema = 55

# balance, stoploss, reward_ratio
ttr = Tester(100_000, 0.001 , 5)
# ticker_data, ticker_size,  ticket_size, small_ema, large_ema
ttr.init(ticker_data, 40_000, small_ema, large_ema)
# small_ema, large_ema
ttr.chart(small_ema, large_ema) 
# run backtesting
ttr.run()
ttr.stats()

t_book2 = ttr.trade_book
profitables = ttr.profitable_trades
losers = ttr.losing_trades

/var/folders/lr/14c6x4yx031bm9r7cfly36_40000gn/T/ipykernel_29302/835503275.py:19: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



TypeError: Backtest.open() got an unexpected keyword argument 'crossover_type'